In [ ]:
!pip install transformers
!pip install wandb
!pip install trl
!pip install pandas
!pip install datasets
!pip install accelerate
!pip install tyro
!pip install nltk -U

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 10.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 195.4/195.4 kB 16.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 264.6/264.6 kB 15.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 7.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 225.0/225.0 kB 3.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 290.1/290.1 kB 27.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 36.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.8/79.8 kB 10.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 26.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 56.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 60.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.7/731.7 MB 2.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━

In [ ]:

import torch
from tqdm import tqdm
import pandas as pd
import wandb
import os

tqdm.pandas()

from transformers import pipeline, AutoTokenizer
from datasets import load_dataset

from trl import PPOTrainer, PPOConfig, AutoModelForCausalLMWithValueHead
from trl.core import LengthSampler


In [ ]:

config = PPOConfig(
    model_name    = "gpt2",
    learning_rate = 1.41e-5,
    ## log_with      = "wandb",
)

sent_kwargs = {
         "return_all_scores": True,
         "function_to_apply": "none",
         "batch_size": 16
}


In [ ]:

## wandb.init()

wandb.init(mode="disabled")
os.environ['WANDB_DISABLED'] = 'true'



## Loading NEWS BIAS dataset

This dataset encompasses multiple dimensions of biases in news media, such as political inclinations, hate speech, toxicity, sexism, ageism, and more, establishing its distinctiveness in the realm of similar datasets. It's noteworthy that the dataset explicitly refrains from including any personally identifiable information (PII).

In [ ]:
import pandas as pd

def truncate_and_save_dataset(original_file_path, truncated_file_path, percentage=0.1):
    # Load the original dataset
    df = pd.read_csv(original_file_path)

    # Keep only specified columns
    df = df[['text','label']]

    # Calculate the number of rows to keep
    nrows_to_keep = int(len(df) * percentage)

    # Truncate the dataset
    truncated_df = df.sample(n=nrows_to_keep, random_state=1)

    # Save the truncated dataset to a new CSV file
    truncated_df.to_csv(truncated_file_path, index=False)
    print(f"Truncated dataset saved to {truncated_file_path}")

# Specify your original and new file paths
train_original_file_path = 'train_dataset.csv'
train_truncated_file_path = 'trunc_train_dataset.csv'

test_original_file_path = 'test_dataset.csv'
test_truncated_file_path = 'trunc_test_dataset.csv'

# Truncate and save the datasets
truncate_and_save_dataset(train_original_file_path, train_truncated_file_path, percentage=0.1)
truncate_and_save_dataset(test_original_file_path, test_truncated_file_path, percentage=0.1)


Truncated dataset saved to trunc_train_dataset.csv
Truncated dataset saved to trunc_test_dataset.csv


In [ ]:
ds = load_dataset('csv', data_files='trunc_train_dataset.csv', split='train')

Generating train split: 0 examples [00:00, ? examples/s]


## Visualize details of dataset


In [ ]:

ds


Dataset({
    features: ['text', 'label'],
    num_rows: 293994
})

In [ ]:

ds[15:18]


{'text': ['Trudeau performed beyond expectations??!  The bar must have been set very low.  The Intellectual Midget has been an embarassment to Canadians',
  'wondering why no one answers my tweets ',
  'Progress has been made DESPITE the resistance of many (white) Americans. It will not take everyone because not everyone will join in getting rid of racism since benefits are derived from certain groups of people being denied rights and privileges. For example, many rural whites work in the prison industry. They have a material stake in maintaining the disproportionate  incarceration rates of non-whites in general and Blacks in particular. \\n"All lives matter" is a truism and therefore pointless as has been aptly pointed out by many above. \\nYou are entirely incorrect that EVERYONE will be necessary to effectuate change. It\'s never been EVERYONE and change will come despite not EVERYONE participating toward that goal. Certain types of white people have and will continue to hinder such

In [ ]:

from datasets import ClassLabel
import random
import pandas as pd
from IPython.display import display, HTML


In [ ]:

def show_random_elements(dataset, num_examples=20):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."

    picks = []

    for _ in range( num_examples ):

        pick = random.randint(0, len(dataset)-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)

    df = pd.DataFrame( dataset[picks] )        ## indexing 10 picks

    print(df)
    print(dataset.features.items())

    for column, typ in dataset.features.items():
        print(column)
        print(typ)
        print(ClassLabel)
        ## The isinstance() function returns True if the specified object
        ## is of the specified type, otherwise False
        if isinstance(typ, ClassLabel):
            print("Hello")
            df[column] = df[column].transform(lambda i: typ.names[i])
            ## print(typ.names[i])

    display(HTML(df.to_html()))


In [ ]:

show_random_elements(ds)


                                                 text            label
0   Apology \n\nA message from my talk page:\nI ca...    Highly Biased
1   Did you read his book, "Shaking Hands with the...    Highly Biased
2   Alex Kaloi played as a freshman and started fo...          Neutral
3   @DerrickWayneJr because no one was on ! i was ...  Slightly Biased
4   Facebook revealed on Sept. 6 that it had found...  Slightly Biased
5   @MisKoChai am I doing this right!?!? I luuvvv ...          Neutral
6   I know from my research that the wind industry...    Highly Biased
7   theDonald must be a  Democrat, then?\nA Liar, ...    Highly Biased
8   Trudeau should have clarified:  the national i...          Neutral
9   On Mr. Lisi's letter  (that IS the subject, ri...    Highly Biased
10  @thatglamchick ok.... tx  it's so worth the wa...          Neutral
11  @FuchsiaStiletto nah, i didnt get no easter eg...  Slightly Biased
12  watching dieguito right now, baby fabian is st...          Neutral
13    

In [ ]:

tokenizer           = AutoTokenizer.from_pretrained(config.model_name)
tokenizer.pad_token = tokenizer.eos_token


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

In [ ]:
def tokenize(sample):
    encoding = tokenizer.encode_plus(
        sample["text"],
        add_special_tokens=True,
        max_length=1024,
        truncation=True,
        padding='max_length',
        return_tensors='pt'
    )

    sample["input_ids"] = encoding["input_ids"].squeeze()[:20]  # Further truncate to 20 tokens for your specific use case
    sample["query"] = tokenizer.decode(sample["input_ids"].tolist())

    return sample
ds = ds.map(tokenize, batched=False)
ds

Map:   0%|          | 0/293994 [00:00<?, ? examples/s]

Dataset({
    features: ['text', 'label', 'input_ids', 'query'],
    num_rows: 293994
})

In [ ]:

ds[15:18]


{'text': ['Trudeau performed beyond expectations??!  The bar must have been set very low.  The Intellectual Midget has been an embarassment to Canadians',
  'wondering why no one answers my tweets ',
  'Progress has been made DESPITE the resistance of many (white) Americans. It will not take everyone because not everyone will join in getting rid of racism since benefits are derived from certain groups of people being denied rights and privileges. For example, many rural whites work in the prison industry. They have a material stake in maintaining the disproportionate  incarceration rates of non-whites in general and Blacks in particular. \\n"All lives matter" is a truism and therefore pointless as has been aptly pointed out by many above. \\nYou are entirely incorrect that EVERYONE will be necessary to effectuate change. It\'s never been EVERYONE and change will come despite not EVERYONE participating toward that goal. Certain types of white people have and will continue to hinder such



    
## Now this for actual RLHF  



In [ ]:
from datasets import Dataset, load_dataset, DatasetDict
from transformers import AutoTokenizer
import pandas as pd

# This is the function for building the dataset from our CSV file which can be used for RLHF
def build_dataset_from_csv(config, train_csv_file_path, test_csv_file_path):
    tokenizer = AutoTokenizer.from_pretrained(config.model_name)
    tokenizer.pad_token = tokenizer.eos_token

    # Load CSV files into Pandas DataFrames
    train_df = pd.read_csv(train_csv_file_path)
    test_df = pd.read_csv(test_csv_file_path)

    # Convert DataFrames into Hugging Face Dataset format
    train_ds = Dataset.from_pandas(train_df)
    test_ds = Dataset.from_pandas(test_df)

    # Combine into DatasetDict
    dataset = DatasetDict({
        'train': train_ds,
        'test': test_ds
    })

    # Define tokenize function
    def tokenize(example):
        result = tokenizer(example['text'], truncation=True, padding='max_length', max_length=512)
        return result

    # Apply tokenize function
    dataset = dataset.map(tokenize, batched=True)

    # Set format for PyTorch
    dataset.set_format(type="torch", columns=['input_ids', 'attention_mask', 'label'])

    return dataset

In [ ]:

dataset = build_dataset_from_csv(config, '/content/trunc_train_dataset.csv','/content/trunc_test_dataset.csv')


Map:   0%|          | 0/293994 [00:00<?, ? examples/s]

Map:   0%|          | 0/73498 [00:00<?, ? examples/s]

In [ ]:

def collator(data):
    return dict((key, [d[key] for d in data]) for key in data[0])



## Load pre-trained GPT2 language models
We load the GPT2 model with a value head and the tokenizer. We load the model twice; the first model is optimized while the second model serves as a reference to calculate the KL-divergence from the starting point. This serves as an additional reward signal in the PPO training to make sure the optimized model does not deviate too much from the original language model.


In [ ]:

model     = AutoModelForCausalLMWithValueHead.from_pretrained(config.model_name)
ref_model = AutoModelForCausalLMWithValueHead.from_pretrained(config.model_name)

tokenizer = AutoTokenizer.from_pretrained(config.model_name)

tokenizer.pad_token = tokenizer.eos_token


model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/548M [00:00<?, ?B/s]

In [ ]:

ppo_trainer = PPOTrainer(
                 config,
                 model,
                 ref_model,
                 tokenizer,
                 dataset=train_dataset,
                 data_collator=collator
)



## Load UnBIAS-classifier (Reward Function)

We load a UnBIAS-classifier fine-tuned on the News Bias dataset.


In [ ]:

device = ppo_trainer.accelerator.device
device


device(type='cpu')

In [ ]:

if ppo_trainer.accelerator.num_processes == 1:
    device = 0 if torch.cuda.is_available() else "cpu"  # to avoid a `pipeline` bug

device

'cpu'

In [ ]:

sentiment_pipe = pipeline("text-classification", model="newsmediabias/UnBIAS-classifier", device=device)


config.json:   0%|          | 0.00/921 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/438M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/366 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]


The model outputs are the logits for the negative and positive class. We will use the logits for positive class as a reward signal for the language model.


In [ ]:

text = "this movie is not good"

sentiment_pipe(text, **sent_kwargs)


[[{'label': 'Highly Biased', 'score': -2.8032827377319336},
  {'label': 'Slightly Biased', 'score': 0.7118046879768372},
  {'label': 'Neutral', 'score': 1.310873031616211}]]

In [ ]:
text = "this movie is horrible"

sentiment_pipe(text, **sent_kwargs)

[[{'label': 'Highly Biased', 'score': 0.46684542298316956},
  {'label': 'Slightly Biased', 'score': 1.1993681192398071},
  {'label': 'Neutral', 'score': -2.3412296772003174}]]

In [ ]:

text = "this movie is damn horrible"
sentiment_pipe(text, **sent_kwargs)


[[{'label': 'Highly Biased', 'score': 2.442782402038574},
  {'label': 'Slightly Biased', 'score': 0.17955872416496277},
  {'label': 'Neutral', 'score': -3.0951590538024902}]]



## Generation settings

For the response generation we just use sampling and make sure top-k and nucleus sampling are turned off as well as a minimal length.


In [ ]:

gen_kwargs = {
         "min_length":   -1,
         "top_k":       0.0,
         "top_p":       1.0,
         "do_sample":  True,
         "pad_token_id": tokenizer.eos_token_id
}



## Optimize model

### Training loop

The training loop consists of the following main steps:

* Get the query and responses from the policy network (GPT-2)
* Get sentiments for query/responses from UnBias
* Optimize policy with PPO using the (query, response, reward) triplet


In [ ]:

output_min_length     = 4
output_max_length     = 16
output_length_sampler = LengthSampler(output_min_length, output_max_length)


In [ ]:

generation_kwargs = {
    "min_length":     -1,
    "top_k":         0.0,
    "top_p":         1.0,
    "do_sample":    True,
    "pad_token_id": tokenizer.eos_token_id,
}


In [ ]:

## ppo_trainer.config.steps = 100    ## 20,000
ppo_trainer.config.steps


20000

In [ ]:

for epoch, batch in tqdm(enumerate(ppo_trainer.dataloader)):
    query_tensors = batch["input_ids"]

    print(query_tensors)
    print(len(query_tensors))
    if epoch == 1:
        break


1it [00:00,  1.91it/s]

[tensor([31369,    71,  6081, 30357,  5145,  1521,   389,   345,   477, 42023,
         1909,    30,   845,  1178,  4130,  6851,   220, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,

1it [00:01,  1.44s/it]

[tensor([   31,    74,  2442,    24,  2078, 42254,    13,  6416,  1143,   326,
          618,   257,  1545,   531,   326,  1165,   986,   887,   339,   338,
          655,  2045,   866,   269, 10277,   339,   338,  9087,   866,   262,
         4831,   220, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,
        50256, 50256, 50256, 50256, 50256, 50256, 50256, 50256,

In [ ]:
for epoch, batch in tqdm(enumerate(ppo_trainer.dataloader)):
    query_tensors = batch["input_ids"]
    print(epoch)
    print(batch)
    print('*********************')
    print('*********************')
    print('*********************')
    print('*********************')
    #### Get response from gpt2
    response_tensors = []
    for query in query_tensors:
        gen_len                             = output_length_sampler()
        generation_kwargs["max_new_tokens"] = gen_len
        response                            = ppo_trainer.generate(query, **generation_kwargs)
        response_tensors.append( response.squeeze()[-gen_len:] )
    batch["response"] = [ tokenizer.decode(r.squeeze()) for r in response_tensors ]
    print(batch)
    if epoch == 1:
        break

0it [00:00, ?it/s]

0


A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


{'label': ['Slightly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Neutral', 'Neutral', 'Slightly Biased', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Highly Biased', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Highly Biased', 'Neutral', 'Highly Biased', 'Neutral', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Highly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Highly Biased', 'Highly Biased', 'Slightly Biased', 'Neutral', 'Neutral', 'Slightly Biased', 'Neutral', 'Neutral', 'Neutral', 'Slightly Biased', 'Neutral', 'Neutral', 'Slightly Biased', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Highly Biased', 'Neutral', 'Neutral'

A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='le

{'label': ['Slightly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Neutral', 'Neutral', 'Slightly Biased', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Highly Biased', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Highly Biased', 'Neutral', 'Highly Biased', 'Neutral', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Highly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Highly Biased', 'Highly Biased', 'Slightly Biased', 'Neutral', 'Neutral', 'Slightly Biased', 'Neutral', 'Neutral', 'Neutral', 'Slightly Biased', 'Neutral', 'Neutral', 'Slightly Biased', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Highly Biased', 'Neutral', 'Neutral'

A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


{'label': ['Neutral', 'Highly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Highly Biased', 'Slightly Biased', 'Neutral', 'Slightly Biased', 'Highly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Highly Biased', 'Slightly Biased', 'Neutral', 'Neutral', 'Neutral', 'Highly Biased', 'Neutral', 'Highly Biased', 'Neutral', 'Neutral', 'Slightly Biased', 'Neutral', 'Highly Biased', 'Highly Biased', 'Highly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Slightly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Highly Biased', 'Neutral', 'Highly Biased', 'Neutral', 'Highly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Highly Biased', 'Neutral', 'Slightly Biased', 'Neutral', 'Highly Biased', 'Highly 

A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='le

{'label': ['Neutral', 'Highly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Highly Biased', 'Slightly Biased', 'Neutral', 'Slightly Biased', 'Highly Biased', 'Slightly Biased', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Highly Biased', 'Slightly Biased', 'Neutral', 'Neutral', 'Neutral', 'Highly Biased', 'Neutral', 'Highly Biased', 'Neutral', 'Neutral', 'Slightly Biased', 'Neutral', 'Highly Biased', 'Highly Biased', 'Highly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Neutral', 'Slightly Biased', 'Slightly Biased', 'Neutral', 'Slightly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Highly Biased', 'Neutral', 'Highly Biased', 'Neutral', 'Highly Biased', 'Neutral', 'Neutral', 'Highly Biased', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Neutral', 'Highly Biased', 'Neutral', 'Slightly Biased', 'Neutral', 'Highly Biased', 'Highly 

In [ ]:

batch.keys()


dict_keys(['label', 'input_ids', 'attention_mask', 'response'])


#### Compute sentiment score


In [ ]:

batch["attention_mask"]


[tensor([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0

In [ ]:

batch["label"]


['Neutral',
 'Neutral',
 'Neutral',
 'Neutral',
 'Neutral',
 'Neutral',
 'Neutral',
 'Highly Biased',
 'Slightly Biased',
 'Highly Biased',
 'Highly Biased',
 'Neutral',
 'Neutral',
 'Neutral',
 'Neutral',
 'Neutral',
 'Highly Biased',
 'Neutral',
 'Neutral',
 'Slightly Biased',
 'Highly Biased',
 'Slightly Biased',
 'Neutral',
 'Neutral',
 'Highly Biased',
 'Slightly Biased',
 'Slightly Biased',
 'Slightly Biased',
 'Neutral',
 'Neutral',
 'Slightly Biased',
 'Neutral',
 'Neutral',
 'Neutral',
 'Slightly Biased',
 'Slightly Biased',
 'Slightly Biased',
 'Slightly Biased',
 'Neutral',
 'Neutral',
 'Highly Biased',
 'Highly Biased',
 'Neutral',
 'Neutral',
 'Neutral',
 'Slightly Biased',
 'Neutral',
 'Slightly Biased',
 'Neutral',
 'Neutral',
 'Neutral',
 'Highly Biased',
 'Highly Biased',
 'Slightly Biased',
 'Slightly Biased',
 'Neutral',
 'Neutral',
 'Neutral',
 'Highly Biased',
 'Neutral',
 'Highly Biased',
 'Highly Biased',
 'Highly Biased',
 'Neutral',
 'Slightly Biased',
 'Highly

In [ ]:

texts = [ q + r for q, r in zip(batch["attention_mask"], batch["response"]) ]


TypeError: unsupported operand type(s) for +: 'Tensor' and 'str'

In [ ]:

texts


['This movie is poorly conceived---Monster Hunter is supposed to',
 'i liked this movie, even though it was released in',
 "The first noticeable problem about Tonto: he was fuelling the characters' personalities at a young age",
 'When I spotted that Noah Wyle had made an early cameo appearance at',
 "Modern viewers know this is a critic's I think",
 'Evidently lots of good plot holes, with a',
 'There are some redeeming qualities that make Paterno work in a',
 'This is a very strange film which can be very',
 'good lord! For the first time, even',
 'This is because a compass and compass (another form of sound cancellation) is used to',
 'You know, it wasn\'t half bad, but it had it all."<|endoftext|>',
 'This is part one of the five sections of the film. There are several humorous remarks that border',
 'I mean of all the obscure French and Irish myths that',
 'Okay first of all - I wanted to see the full length',
 'Not that many films have truly had a "Stalker" moment," but Seidl doe

In [ ]:

pipe_outputs = sentiment_pipe(texts, **sent_kwargs)
pipe_outputs


[[{'label': 'NEGATIVE', 'score': 2.2946932315826416},
  {'label': 'POSITIVE', 'score': -2.7317020893096924}],
 [{'label': 'NEGATIVE', 'score': -1.925742506980896},
  {'label': 'POSITIVE', 'score': 2.2019805908203125}],
 [{'label': 'NEGATIVE', 'score': -0.18878592550754547},
  {'label': 'POSITIVE', 'score': -0.011356303468346596}],
 [{'label': 'NEGATIVE', 'score': -0.01333677675575018},
  {'label': 'POSITIVE', 'score': -0.11825768649578094}],
 [{'label': 'NEGATIVE', 'score': -1.9098631143569946},
  {'label': 'POSITIVE', 'score': 2.153944730758667}],
 [{'label': 'NEGATIVE', 'score': -1.0707851648330688},
  {'label': 'POSITIVE', 'score': 1.1191564798355103}],
 [{'label': 'NEGATIVE', 'score': -1.4140279293060303},
  {'label': 'POSITIVE', 'score': 1.6278727054595947}],
 [{'label': 'NEGATIVE', 'score': -1.9853274822235107},
  {'label': 'POSITIVE', 'score': 2.2685697078704834}],
 [{'label': 'NEGATIVE', 'score': -1.6584359407424927},
  {'label': 'POSITIVE', 'score': 1.8835939168930054}],
 [{'l

In [ ]:

rewards = [ torch.tensor(output[1]["score"]) for output in pipe_outputs]
rewards


[tensor(-2.7317),
 tensor(2.2020),
 tensor(-0.0114),
 tensor(-0.1183),
 tensor(2.1539),
 tensor(1.1192),
 tensor(1.6279),
 tensor(2.2686),
 tensor(1.8836),
 tensor(-0.2499),
 tensor(1.4789),
 tensor(1.3212),
 tensor(0.2753),
 tensor(1.0822),
 tensor(0.8769),
 tensor(1.6423),
 tensor(0.7947),
 tensor(1.6409),
 tensor(2.6443),
 tensor(-0.7279),
 tensor(2.3880),
 tensor(-1.0589),
 tensor(2.3231),
 tensor(-1.1874),
 tensor(2.7740),
 tensor(-0.5302),
 tensor(2.6618),
 tensor(-0.1971),
 tensor(-0.1593),
 tensor(1.9095),
 tensor(-0.0538),
 tensor(1.9543),
 tensor(-1.1134),
 tensor(0.5438),
 tensor(-1.5954),
 tensor(0.1579),
 tensor(-1.8283),
 tensor(1.7351),
 tensor(-0.1821),
 tensor(-1.6691),
 tensor(-1.7416),
 tensor(0.7545),
 tensor(-1.8997),
 tensor(1.0599),
 tensor(-2.6420),
 tensor(0.3579),
 tensor(1.1189),
 tensor(-0.8248),
 tensor(2.8067),
 tensor(-2.7147),
 tensor(-2.6384),
 tensor(-2.2516),
 tensor(0.0565),
 tensor(1.4536),
 tensor(1.7251),
 tensor(2.6113),
 tensor(-0.4088),
 tensor

In [ ]:

len(rewards)


128

In [ ]:

for epoch, batch in tqdm(enumerate(ppo_trainer.dataloader)):
    query_tensors = batch["input_ids"]
    print(epoch)

    #### Get response from gpt2
    response_tensors = []
    for query in query_tensors:
        gen_len                             = output_length_sampler()
        generation_kwargs["max_new_tokens"] = gen_len
        response                            = ppo_trainer.generate(query, **generation_kwargs)
        response_tensors.append( response.squeeze()[-gen_len:] )
    batch["response"] = [ tokenizer.decode(r.squeeze()) for r in response_tensors ]

    #### Compute sentiment score
    texts = [q + r for q, r in zip(batch["query"], batch["response"])]
    pipe_outputs = sentiment_pipe(texts, **sent_kwargs)
    rewards = [ torch.tensor(output[1]["score"]) for output in pipe_outputs]

    #### Run PPO step
    stats = ppo_trainer.step(
                     query_tensors,
                     response_tensors,
                     rewards
    )
    ppo_trainer.log_stats(stats, batch, rewards)



0it [00:00, ?it/s]

0


1it [00:09,  9.49s/it]

1


2it [00:19,  9.86s/it]

...

192it [33:20, 10.29s/it]

192


193it [33:30, 10.32s/it]

193


194it [33:40, 10.42s/it]


In [ ]:

torch.cuda.get_device_name(0)


'NVIDIA A30'


One can observe how the model starts to generate more positive outputs after a few optimisation steps.

Note: Investigating the KL-divergence will probably show that at this point the model has not converged to the target KL-divergence, yet. To get there would require longer training or starting with a higher initial coefficient.



Let's inspect some examples from the IMDB dataset. We can use model_ref to compare the tuned model model against the model before optimisation.


In [ ]:

#### get a batch from the dataset
bs                 = 16
game_data          = dict()


In [ ]:

game_data


{}

In [ ]:

dataset.set_format("pandas")


In [ ]:

df_batch           = dataset[:].sample(bs)
df_batch


review  label  \
9325   Well I guess I know the answer to that questio...      0   
23943  This is an excellent, fast paced thriller by W...      1   
10309  Now, I flicked onto this just out of curiosity...      0   
14702  We tend to forget that the master/slave contex...      1   
4466   The proverb "Never judge a book by it's cover"...      0   
8982   I've never understood the appeal of Garbo. She...      0   
14943  Hugh (Ed Harris) is a hotshot, bachelor senato...      1   
16515  This particular Joe McDoakes short subject was...      1   
13573  Sisters In Law is made by the same directors o...      1   
16473  I was very fond of this film. It kept me guess...      1   
10149  If he wanted to be accurate, he should have ch...      0   
20765  Thats My Bush is first of all a very entertain...      1   
16242  This is possibly the best short crime drama I'...      1   
18014  Some people say this is the best film that PRC...      1   
2193   A remake of Alejandro Amenabar's Abre los Ojos...      0   
8591   What a terrible film. It sucked. It was terrib...      0   

                                     input_ids  \
9325                               [5779, 314]   
23943         [1212, 318, 281, 6275, 11, 3049]   
10309                     [3844, 11, 314, 781]   
14702        [1135, 4327, 284, 6044, 326, 262]   
4466                              [464, 36950]   
8982                    [40, 1053, 1239, 7247]   
14943             [39, 6724, 357, 7407, 10026]   
16515                 [1212, 1948, 5689, 1982]   
13573     [50, 6223, 554, 3854, 318, 925, 416]   
16473               [40, 373, 845, 16245, 286]   
10149        [1532, 339, 2227, 284, 307, 7187]   
20765                              [817, 1381]   
16242                   [1212, 318, 5457, 262]   
18014               [4366, 661, 910, 428, 318]   
2193                          [32, 28763, 286]   
8591   [2061, 257, 7818, 2646, 13, 632, 25669]   

                                 query  
9325                            Well I  
23943       This is an excellent, fast  
10309                        Now, I fl  
14702       We tend to forget that the  
4466                       The proverb  
8982             I've never understood  
14943                  Hugh (Ed Harris  
16515           This particular Joe Mc  
13573        Sisters In Law is made by  
16473               I was very fond of  
10149      If he wanted to be accurate  
20765                            Thats  
16242             This is possibly the  
18014          Some people say this is  
2193                       A remake of  
8591   What a terrible film. It sucked

In [ ]:

game_data["query"] = df_batch["query"].tolist()
query_tensors      = df_batch["input_ids"].tolist()


In [ ]:

response_tensors_ref, response_tensors = [], []


In [ ]:

#### get response from gpt2 and gpt2_ref
for i in range(bs):
    gen_len = output_length_sampler()

    output  = ref_model.generate(
        torch.tensor(query_tensors[i]).unsqueeze(dim=0).to(device), max_new_tokens=gen_len, **gen_kwargs
    ).squeeze()[-gen_len:]
    response_tensors_ref.append(output)


    output = model.generate(
        torch.tensor(query_tensors[i]).unsqueeze(dim=0).to(device), max_new_tokens=gen_len, **gen_kwargs
    ).squeeze()[-gen_len:]
    response_tensors.append(output)


In [ ]:

#### decode responses
game_data["response (before)"] = [tokenizer.decode(response_tensors_ref[i]) for i in range(bs)]
game_data["response (after)"]  = [tokenizer.decode(response_tensors[i]) for i in range(bs)]


In [ ]:

#### sentiment analysis of query/response pairs before/after
texts = [q + r for q, r in zip(game_data["query"], game_data["response (before)"])]
game_data["rewards (before)"] = [output[1]["score"] for output in sentiment_pipe(texts, **sent_kwargs)]


/home/rcalix/.local/lib/python3.8/site-packages/transformers/pipelines/text_classification.py:105: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(
/home/rcalix/.local/lib/python3.8/site-packages/transformers/pipelines/base.py:1123: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


In [ ]:

texts = [q + r for q, r in zip(game_data["query"], game_data["response (after)"])]
game_data["rewards (after)"] = [output[1]["score"] for output in sentiment_pipe(texts, **sent_kwargs)]


In [ ]:

# store results in a dataframe
df_results = pd.DataFrame(game_data)
df_results


query  \
0                            Well I   
1        This is an excellent, fast   
2                         Now, I fl   
3        We tend to forget that the   
4                       The proverb   
5             I've never understood   
6                   Hugh (Ed Harris   
7            This particular Joe Mc   
8         Sisters In Law is made by   
9                I was very fond of   
10      If he wanted to be accurate   
11                            Thats   
12             This is possibly the   
13          Some people say this is   
14                      A remake of   
15  What a terrible film. It sucked   

                                    response (before)  \
0                                 don't know why they   
1                 -paced ride, with big action scenes   
2                             inched. It was so wrong   
3                             picture itself was wish   
4    on the Désir de Rathmeister's installation wa...   
5                          more by this point in your   
6                          , "The Hurt Locker") helps   
7                       Avoy came into her film as if   
8    Donna Hawley and Lauren Ridge. The two stars ...   
9       Korea. I love all of their eccentricities. My   
10                                      on his pitch,   
11     sorry this movie is so stupid!!! seriously why   
12   worst addiction film out of its annoying rang...   
13           pure comedy, that is, if you believe the   
14                                  "The Wizard of Oz   
15   terrible film. It sucked. A very enjoyable fi...   

                                     response (after)  rewards (before)  \
0                           love THIS, wonderful film         -1.327288   
1       moving story with a nice idea of contemporary          2.836497   
2                   ocked to this hilarious show, and         -1.446260   
3                                 movie is thrilling,         -0.736429   
4    keeps a very pleasant note...well written.(19...          0.274140   
5             this wonderful script & still encourage          1.372031   
6                  ) is marvelous and fictional. It's          0.467258   
7            Govern shone, with his Voyager light and          1.329040   
8    a group of filmmakers who gave Lawrence Sim's...          1.828336   
9    her throughout you really, now very fond of. She          2.317214   
10                           you see this intelligent         -0.509769   
11            and Sally are an excellent mix - one of         -1.907444   
12   finest drama I have seen filmed, and you'll s...         -2.723184   
13   a very generous film and, despite what collea...          1.589134   
14                           one of my favorite films          0.292409   
15  , but great! Love it...and particular love the...         -0.659871   

    rewards (after)  
0          2.887235  
1          2.924836  
2          2.764766  
3          2.090948  
4          2.469272  
5          2.755003  
6          2.578309  
7          2.701365  
8          2.651180  
9          2.652236  
10         1.797603  
11         2.824260  
12         2.707408  
13         2.410795  
14         2.371585  
15         1.632155

In [ ]:

print("mean:")
display(df_results[["rewards (before)", "rewards (after)"]].mean())
print()
print("median:")
display(df_results[["rewards (before)", "rewards (after)"]].median())



mean:


rewards (before)    0.187238
rewards (after)     2.513685
dtype: float64


median:


rewards (before)    0.283274
rewards (after)     2.651708
dtype: float64

In [ ]:

## model.save_pretrained(    "gpt2-imdb-pos-v2", push_to_hub=True)
## tokenizer.save_pretrained("gpt2-imdb-pos-v2", push_to_hub=True)

model.save_pretrained(    "gpt2-imdb-pos-v2", push_to_hub=False)
tokenizer.save_pretrained("gpt2-imdb-pos-v2", push_to_hub=False)



('gpt2-imdb-pos-v2/tokenizer_config.json',
 'gpt2-imdb-pos-v2/special_tokens_map.json',
 'gpt2-imdb-pos-v2/vocab.json',
 'gpt2-imdb-pos-v2/merges.txt',
 'gpt2-imdb-pos-v2/added_tokens.json',
 'gpt2-imdb-pos-v2/tokenizer.json')